In [1]:
import glob
import ujson

In [2]:
! wget http://mklab2.iti.gr/multisensor/images/5/5c/WikiRef_dataset.zip

--2020-04-27 18:20:02--  http://mklab2.iti.gr/multisensor/images/5/5c/WikiRef_dataset.zip
Resolving mklab2.iti.gr (mklab2.iti.gr)... 160.40.50.223
Connecting to mklab2.iti.gr (mklab2.iti.gr)|160.40.50.223|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1345469 (1,3M) [application/zip]
Saving to: ‘WikiRef_dataset.zip’

WikiRef_dataset.zip 100%[===================>]   1,28M  2,32MB/s    in 0,6s    

2020-04-27 18:20:03 (2,32 MB/s) - ‘WikiRef_dataset.zip’ saved [1345469/1345469]



In [3]:
! unzip -q WikiRef_dataset.zip 
! cat WikiRef_dataset/readme.txt


In [4]:
! ls WikiRef_dataset/WikiRef220

 barack.obama.1.txt		   'ParisAttacks2015 (21).txt'
 barack.obama.24.txt		   'ParisAttacks2015 (22).txt'
 barack.obama.3.txt		   'ParisAttacks2015 (23).txt'
 barack.obama.4.txt		   'ParisAttacks2015 (24).txt'
 barack.obama.9.txt		   'ParisAttacks2015 (25).txt'
 cypriot.financial.crisis.36.txt   'ParisAttacks2015 (26).txt'
 cypriot.financial.crisis.37.txt   'ParisAttacks2015 (27).txt'
 cypriot.financial.crisis.38.txt   'ParisAttacks2015 (28).txt'
 cypriot.financial.crisis.39.txt   'ParisAttacks2015 (29).txt'
 cypriot.financial.crisis.40.txt   'ParisAttacks2015 (2).txt'
 debt.crisis.greece.178.txt	   'ParisAttacks2015 (30).txt'
 debt.crisis.greece.179.txt	   'ParisAttacks2015 (31).txt'
 debt.crisis.greece.207.txt	   'ParisAttacks2015 (32).txt'
 debt.crisis.greece.263.txt	   'ParisAttacks2015 (33).txt'
 debt.crisis.greece.81.txt	   'ParisAttacks2015 (34).txt'
 greek.elections.112.txt	   'ParisAttacks2015 (35).txt'
 greek.elections.113.txt	   'ParisAttacks2015 (36).txt'
 greek.elections.11

In [5]:
import nltk
import string

import pandas as pd
from glob import glob



In [6]:
nltk.data.path.append('/home/evgenyegorov/nltk_data/')

In [7]:
dir_name = "WikiRef_dataset/WikiRef220"
files = glob(dir_name + '/*.txt')


In [8]:
! cat WikiRef_dataset/WikiRef220/smartphone.107.txt


In [9]:
from nltk.corpus import wordnet

def nltk2wn_tag(nltk_tag):
    if nltk_tag.startswith('J'):
        return wordnet.ADJ
    elif nltk_tag.startswith('V'):
        return wordnet.VERB
    elif nltk_tag.startswith('N'):
        return wordnet.NOUN
    elif nltk_tag.startswith('R'):
        return wordnet.ADV
    else:          
        return ''

In [10]:
from ftfy import fix_text

data = []
for path in files:
    entry = {}
    entry['id'] = path.split('/')[-1].rpartition(".")[0]
    with open(path, 'r', encoding="Latin") as f:
        entry['raw_text'] = " ".join(fix_text(line).strip() for line in f)
    data.append(entry)

texts = pd.DataFrame(data)

In [11]:
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords
stop = set(stopwords.words('english'))

wnl = WordNetLemmatizer()


In [12]:
import sys
sys.path.append('../clustering_system/')

import re
import os
import pymorphy2
from collections import Counter

from preprocessing.aitexta.tokenization import RegexpTokenizer
from preprocessing.aitexta.tokenization import SpacyRulesRussianTokenizer
from preprocessing.aitexta.utils import FunctionalTransformer
from preprocessing.aitexta.lemmatization import Pymorphy2Lemmatizer
from preprocessing.aitexta.feature_filtering import StopTokensRemover
from preprocessing.aitexta.feature_filtering import RegexpFilter
from preprocessing.aitexta.feature_filtering import BASE_RU_NONTOKEN_REGEXPS
from preprocessing.aitexta.feature_extracting import TopMineNgrammer
from preprocessing.aitexta.ner_extracting import Pymorphy2NerExtractor
from preprocessing.aitexta.utils import MergerTransformer
from preprocessing.aitexta.pipeline import SequentialPipeline

In [13]:
this_file_path = os.path.dirname('../clustering_system/preprocessing/')
STOP_TOKENS_RELATIVE_PATH = 'aitexta/feature_filtering/stop_words_files/BASE_UNIVERSAL.txt'
STOP_TOKENS_FILE = os.path.join(this_file_path, STOP_TOKENS_RELATIVE_PATH)

In [14]:
# TODO
# specSymb = {"«", "»", "—", "“", "-", "№"}
# specSymb =  punctuation + "«»—“-№"
# pattern = re.compile("[" + re.escape(specSymb) + "]")


In [15]:

def tokenize(text):
    tokens = nltk.wordpunct_tokenize(text.lower())
    return nltk.pos_tag(tokens)

def lemmatize(text):
    lemmatized = [wnl.lemmatize(word,nltk2wn_tag(pos))
                  if nltk2wn_tag(pos) != ''
                  else wnl.lemmatize(word)
                  for word, pos in text ]
    lemmatized = [word for word in lemmatized 
                  if word not in stop and word.isalpha()]
    return lemmatized


class NGrammPreprocessor:
    def __init__(self, n_jobs=1, verbose=False):
        nltk_tokenizer = FunctionalTransformer(tokenize)
        nltk_lemmatizer = FunctionalTransformer(lemmatize)
        
        self.text_to_lemmatized = SequentialPipeline(steps=[
            ('tokenization', nltk_tokenizer),
            ('lemmatization', nltk_lemmatizer),
        ], verbose=verbose)

        self.lemmatized_to_ngramms = SequentialPipeline(steps=[
            ('ngrammer', TopMineNgrammer(stop_tokens_file=STOP_TOKENS_FILE,
                                         nontoken_regexps=None,
                                         allow_delimiters_in_ngramm=True,
                                         output_type='string_ngramm',
                                         n_jobs=n_jobs))
        ], verbose=verbose)

    def fit_transform(self, X):
        X = self._clean_dataframe(X)

        X['lemmatized'] = self.text_to_lemmatized.fit_transform(X['raw_text'].values)

        X['ngramms'] = self.lemmatized_to_ngramms.fit_transform(X['lemmatized'].values)

        for column in ['lemmatized', 'ngramms']:
            X[column] = X[column].apply(lambda x: " ".join(x))

        return X

    def transform(self, X):
        X = self._clean_dataframe(X)

        X['lemmatized'] = self.text_to_lemmatized.transform(X['raw_text'].values)

        X['ngramms'] = self.lemmatized_to_ngramms.transform(X['lemmatized'].values)

        for column in ['lemmatized', 'ngramms']:
            X[column] = X[column].apply(lambda x: " ".join(x))

        return X

    def _clean_dataframe(self, X):
        X['raw_text'] = X['raw_text'].astype(str).str.strip()
        X = X[X['raw_text'] != '']

        return X

In [16]:
preprocesser = NGrammPreprocessor(n_jobs=10, verbose=True)
wiki_processed = preprocesser.fit_transform(texts)

Start of pipeline
**************************************************************************

Start of tokenization fit transform
End of tokenization fit transform
Total time: 6.8257880210876465
----------------------------------------------------------------------
Start of lemmatization fit transform
End of lemmatization fit transform
Total time: 2.13810396194458
----------------------------------------------------------------------
End of pipeline
Total time: 8.972941160202026
----------------------------------------------------------------------
**************************************************************************

Start of pipeline
**************************************************************************

Start of ngrammer fit transform
End of ngrammer fit transform
Total time: 3.967646598815918
----------------------------------------------------------------------
End of pipeline
Total time: 3.968014717102051
------------------------------------------------------------------

In [17]:
wiki_processed.head()

id                                           raw_text  \
0         smartphone.107  The secret behind poor smartphone battery life...   
1  ParisAttacks2015 (28)  On the run from Isis: Jihadists 'targeting Par...   
2     michelle.obama.103  Michelle Obama Goes Organic and Brings in the ...   
3      premier.league.61  Premiership stays on BBC  The BBC has won the ...   
4  ParisAttacks2015 (10)  Hollande says Paris attacks 'an act of war' by...   

                                          lemmatized  \
0  secret behind poor smartphone battery life sum...   
1  run isi jihadist target paris attacker salah a...   
2  michelle obama go organic bring bee go organic...   
3  premiership stay bbc bbc win right show premie...   
4  hollande say paris attack act war islamic stat...   

                                             ngramms  
0  battery_life battery_life battery_life battery...  
1  run_isi run_isi paris_attacker salah_abdeslam ...  
2  michelle_obama michelle_obama white_house whit...  
3  premier_league premier_league premier_league p...  
4  paris_attack act_war act_war act_war islamic_s...

In [18]:
wiki_processed['title'] = wiki_processed.id.str.replace(':', '&#58;').replace('@', '&#64;').replace(' ', '_')




In [22]:
ALL_MODALITIES = ['lemmatized', 'ngramms']
PLAIN_TEXT = "raw_text"




def create_vowpal_wabbit(data, modalities=None, use_counters=False):

    documents_bag = dict()

    for elem_id, elem in data.iterrows():
        if use_counters:
            documents_bag[elem_id] = {m: Counter() for m in ALL_MODALITIES}
        else:
            documents_bag[elem_id] = {m: '' for m in ALL_MODALITIES}
        documents_bag[elem_id]['plain_text'] = ''

        if isinstance(elem[PLAIN_TEXT], str):
            documents_bag[elem_id]['plain_text'] += ' '.join(elem[PLAIN_TEXT].split()) + ' | '

        for modality in ALL_MODALITIES:
            if isinstance(elem[modality], str):
                tokens = elem[modality].split()
                tokens = [re.sub('[\:\|\@]', '', token) for token in tokens]
            elif isinstance(elem[modality], list):
                tokens = [
                    re.sub('[\:\|\@ ]', '_', token.strip())
                    for token in elem[modality]
                ]

            if use_counters:
                documents_bag[elem_id][modality] += Counter(tokens)
            else:
                documents_bag[elem_id][modality] += ' '.join(tokens)

    documents_bag_str_format = []

    for key in documents_bag.keys():
        new_message_str_format = str(key).replace(" ", "_")
        if modalities is None:
            modalities = documents_bag[key].keys()
        for modality in modalities:
            if modality == 'plain_text':
                continue
            if use_counters:
                modality_content = ' '.join([
                    token + ':' + str(count)
                    for token, count in documents_bag[key][modality].items()
                ])
            else:
                modality_content = documents_bag[key][modality]
            new_message_str_format += " |@{} {}".format(modality, modality_content)
        documents_bag_str_format.append(new_message_str_format)
    return documents_bag_str_format



In [28]:
for mode in ["bow", "natural_order"]:

    use_counters = True if mode == "bow" else False
    documents_str_format = create_vowpal_wabbit(wiki_processed.set_index("title"), use_counters=use_counters)

    output = f'wiki_ref220_{mode}'

    with open(output + '.txt', 'w') as f:
        for elem in documents_str_format:
            f.write(elem + '\n')
    wiki_processed["vw_text"] = documents_str_format
    wiki_processed[['id', 'raw_text', 'vw_text']].to_csv(output + '.csv', index=False)

In [29]:
wiki_processed[['id', 'raw_text', 'vw_text']]

id  \
0                  smartphone.107   
1           ParisAttacks2015 (28)   
2              michelle.obama.103   
3               premier.league.61   
4           ParisAttacks2015 (10)   
5               premier.league.21   
6          debt.crisis.greece.263   
7            samsung.galaxy.s5.30   
8                   smartphone.74   
9           ParisAttacks2015 (17)   
10              premier.league.22   
11           samsung.galaxy.s5.39   
12    cypriot.financial.crisis.36   
13              michelle.obama.80   
14             michelle.obama.123   
15          ParisAttacks2015 (12)   
16           samsung.galaxy.s5.42   
17           samsung.galaxy.s5.29   
18          ParisAttacks2015 (32)   
19              michelle.obama.95   
20              premier.league.89   
21              michelle.obama.56   
22                 barack.obama.3   
23           samsung.galaxy.s5.38   
24    malaysia.airlines.flight.86   
25          ParisAttacks2015 (29)   
26             premier.league.143   
27             michelle.obama.102   
28          ParisAttacks2015 (19)   
29    malaysia.airlines.flight.16   
..                            ...   
190           greek.elections.117   
191   malaysia.airlines.flight.34   
192           stephen.hawking.275   
193   malaysia.airlines.flight.31   
194             premier.league.79   
195         ParisAttacks2015 (14)   
196  malaysia.airlines.flight.142   
197          ParisAttacks2015 (7)   
198             premier.league.92   
199             michelle.obama.86   
200              premier.league.9   
201                barack.obama.1   
202   malaysia.airlines.flight.10   
203  malaysia.airlines.flight.227   
204              premier.league.4   
205          samsung.galaxy.s5.27   
206            michelle.obama.100   
207          ParisAttacks2015 (4)   
208             premier.league.63   
209            premier.league.141   
210           samsung.galaxy.s5.4   
211             michelle.obama.75   
212         ParisAttacks2015 (25)   
213            michelle.obama.109   
214          samsung.galaxy.s5.13   
215            michelle.obama.114   
216   malaysia.airlines.flight.32   
217          samsung.galaxy.s5.22   
218  malaysia.airlines.flight.143   
219  malaysia.airlines.flight.225   

                                              raw_text  \
0    The secret behind poor smartphone battery life...   
1    On the run from Isis: Jihadists 'targeting Par...   
2    Michelle Obama Goes Organic and Brings in the ...   
3    Premiership stays on BBC  The BBC has won the ...   
4    Hollande says Paris attacks 'an act of war' by...   
5    Power of top four concerns Keegan  Keegan has ...   
6    Not Out of The Woods Yet: Despite Progress, Eu...   
7    How Google Used Motorola To Smack Down Samsung...   
8    Samsung Waves away a million  KOREAN ELECTRONI...   
9    Behind François Hollande's Snap Decision at St...   
10   Scudamore defends 'boring' League  Premier Lea...   
11   Samsung Galaxy S5 Active just got a 'Sport'-y ...   
12   Criminals IN Government: Cyprus President's Fa...   
13   Michelle Obama celebrates Chicago roots  DENVE...   
14   Michelle Obama, Rihanna Named To People's Best...   
15   France Unsure if Raid Killed Top Suspect in Pa...   
16   Samsung: Galaxy S5 sales stronger than Galaxy ...   
17   Google Has Strangled The Innovation Out Of The...   
18   Paris attacks: France mobilises 115,000 securi...   
19   First Lady Michelle Obama  When people ask Fir...   
20   It's official - Tottenham have the worst defen...   
21   Michelle Obama: Mom First, Political Wife Seco...   
22   Though Obama Had to Leave to Find Himself, It ...   
23   Samsung Galaxy S5 Active (AT&T)  By Eugene Kim...   
24   Flight 370 search area shifts after 'credible ...   
25   Paris attacks were carried out by three groups...   
26   Blues wrap up Torres deal   Chelsea have compl...   
27   Bring Back Our Girls: Michelle Obama and Malal...   
28   France players praised for staying with German...

In [31]:
! head wiki_ref220_bow.csv -n 2

id,raw_text,vw_text
smartphone.107,"The secret behind poor smartphone battery life  Summary:That shiny new smartphone has a battery that easily lasts all day. Then it all goes downhill from there  Rapidly deteriorating battery life has long been tolerated by smartphone owners, mainly because they have no choice. Phones usually meet the holy grail of battery life, the ability to last all day, at first. Then it starts getting worse quickly, until many phone owners end up plugging in during the day. It seems it's always been this way, and there's no incentive to the smartphone makers to make this better.  Battery has long been the focus of the mobile segment. In the early days of mobile the possible time away from a power outlet was not very long. This prompted OEMs to do what they could to make batteries in mobile devices last longer.  This is why we now have decent battery life with most laptops and tablets. The eight hours needed to go all day no matter what comes up is now met by many

In [32]:
! head wiki_ref220_natural_order.csv -n 2

id,raw_text,vw_text
smartphone.107,"The secret behind poor smartphone battery life  Summary:That shiny new smartphone has a battery that easily lasts all day. Then it all goes downhill from there  Rapidly deteriorating battery life has long been tolerated by smartphone owners, mainly because they have no choice. Phones usually meet the holy grail of battery life, the ability to last all day, at first. Then it starts getting worse quickly, until many phone owners end up plugging in during the day. It seems it's always been this way, and there's no incentive to the smartphone makers to make this better.  Battery has long been the focus of the mobile segment. In the early days of mobile the possible time away from a power outlet was not very long. This prompted OEMs to do what they could to make batteries in mobile devices last longer.  This is why we now have decent battery life with most laptops and tablets. The eight hours needed to go all day no matter what comes up is now met by many